In [15]:
import nltk
import re
import torch
from torch.nn.utils.rnn import pad_sequence
from collections import Counter
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd

nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to C:\Users\Jimmy
[nltk_data]     Han\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to C:\Users\Jimmy
[nltk_data]     Han\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to C:\Users\Jimmy
[nltk_data]     Han\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [3]:
# modify this for training data
descriptions = [
    "Spacious 5-bedroom house with a fireplace and a private garden, priced at $850,000.",
    "Charming 3-bedroom cottage with a large front yard and mountain views.",
    "Contemporary 2-bedroom loft, close to shops and cafes, available for $450,000.",
    "Elegant 8-bedroom mansion with a home theater and a tennis court.",
    "Modern 4-bedroom apartment in the city center with balcony views, priced at $700,000.",
    "Stylish 7-bedroom villa with an outdoor jacuzzi and oceanfront views.",
    "Bright 2-bedroom condo near the park and public transport, available for $320,000.",
    "Newly renovated 3-bedroom home with a spacious garage and a garden.",
    "Luxury penthouse with 5 bedrooms, a private pool, and 360-degree city views, on the market for $5 million.",
    "Cozy 1-bedroom studio, walking distance from the beach and restaurants.",
    "Beautiful 6-bedroom house with a large backyard and a barbecue area, listed for $1.4 million.",
    "3-bedroom townhouse with a rooftop garden and great neighborhood amenities.",
    "4-bedroom flat in a quiet residential area, perfect for families, priced at $600,000.",
    "Two-bedroom apartment with an open-plan living area and a balcony.",
    "Stunning 5-bedroom estate with a vineyard and private lake, on sale for $2.8 million.",
    "Urban 2-bedroom apartment with a gym and rooftop access, listed for $485,000.",
    "Spacious 3-bedroom house with a finished basement and large deck.",
    "Rustic 4-bedroom cabin surrounded by nature with a private trail, available for $400,000.",
    "Modern 3-bedroom home with a smart kitchen and home office space.",
    "3-bedroom duplex with a garage and a beautiful garden patio, priced at $475,000.",
    "Luxury 5-bedroom villa with marble floors and a heated swimming pool, on the market for $4.5 million.",
    "Charming 2-bedroom house with vintage design and a lush garden.",
    "Bright 6-bedroom apartment with an open-plan kitchen and living room, listed for $725,000.",
    "Large 4-bedroom home with a home gym and a movie room.",
    "Cosy 1-bedroom flat with a modern kitchen and a walk-in closet, priced at $270,000.",
]

In [16]:
file_path = 'cleaned_data.csv'  # Replace with your CSV file path
data = pd.read_csv(file_path)

# Initialize the list to store descriptions
descriptions = []

# Process each row in the CSV
for _, row in data.iterrows():
    # Convert the row into a string
    description = row['Details']  # Replace 'Details' with your column name if different
    descriptions.append(description)

# Output the result
#print(descriptions)

In [21]:
def preprocess_text(text):
    """
    Preprocess a single text string.
    """
    lemmatizer = WordNetLemmatizer()
    stop_words = set(stopwords.words('english'))
    
    # Lowercase text
    text = text.lower()
    
    text = re.sub(r'[^a-z0-9\s-]', '', text)
    
    # Tokenize text
    tokens = word_tokenize(text)
    
    # Remove stopwords and lemmatize
    tokens = [lemmatizer.lemmatize(word) for word in tokens if word not in stop_words]
    
    return tokens

# Apply preprocessing to descriptions
processed_descriptions = [preprocess_text(desc) for desc in descriptions]
print("Processed Tokens:", processed_descriptions)

Processed Tokens: [['foreclosure168000bedrooms', 'bathroomsbedrooms', '3bathrooms', '2full', 'bathroom', '2main', 'level', 'bathroom', '2main', 'level', 'bedroom', '3basementarea', '0heatingnonecoolingnoneappliancesincluded', 'hot', 'waterhttpswwwzillowcomhomedetails114-evelyn-ave-hamilton-nj-0861938966785zpid'], ['179900602', '3rd', 'ave', 'deptford', 'nj', '08096bedrooms', 'bathroomsbedrooms', '2bathrooms', '1full', 'bathroom', '1main', 'level', 'bathroom', '1main', 'level', 'bedroom', '2roomsroom', 'type', 'living', 'room', 'primary', 'bedroom', 'kitchen', 'bedroom', '1', 'otherheatingforced', 'air', 'natural', 'gascoolingcentral', 'ac', 'natural', 'gasappliancesincluded', 'gas', 'water', 'heaterlaundry', 'main', 'levelhttpswwwzillowcomhomedetails602-3rd-ave-deptford-nj-0809638761090zpid'], ['foreclosure199900bedrooms', 'bathroomsbedrooms', '3bathrooms', '2full', 'bathroom', '2heatingpropanecoolinghas', 'cooling', 'yeslotsize', '374', 'acresdimensions', '374', 'acresdetailsparcel', 

In [22]:
def build_vocab(tokenized_texts, min_freq=1):
    """
    Build a vocabulary dictionary from tokenized texts.
    """
    word_counts = Counter([token for text in tokenized_texts for token in text])
    vocab = {word: idx + 1 for idx, (word, count) in enumerate(word_counts.items()) if count >= min_freq}  # Index starts at 1
    vocab["<PAD>"] = 0  # Padding token
    return vocab

# Create vocabulary
vocab = build_vocab(processed_descriptions, min_freq=1)
print("Vocabulary:", vocab)

# Convert tokens to indices
def tokens_to_indices(tokenized_texts, vocab):
    """
    Convert tokenized texts to sequences of indices based on the vocabulary.
    """
    return [[vocab.get(token, 0) for token in text] for text in tokenized_texts]

# Convert descriptions to indices
indexed_descriptions = tokens_to_indices(processed_descriptions, vocab)
print("Indexed Descriptions:", indexed_descriptions)

Vocabulary: {'foreclosure168000bedrooms': 1, 'bathroomsbedrooms': 2, '3bathrooms': 3, '2full': 4, 'bathroom': 5, '2main': 6, 'level': 7, 'bedroom': 8, '3basementarea': 9, '0heatingnonecoolingnoneappliancesincluded': 10, 'hot': 11, 'waterhttpswwwzillowcomhomedetails114-evelyn-ave-hamilton-nj-0861938966785zpid': 12, '179900602': 13, '3rd': 14, 'ave': 15, 'deptford': 16, 'nj': 17, '08096bedrooms': 18, '2bathrooms': 19, '1full': 20, '1main': 21, '2roomsroom': 22, 'type': 23, 'living': 24, 'room': 25, 'primary': 26, 'kitchen': 27, '1': 28, 'otherheatingforced': 29, 'air': 30, 'natural': 31, 'gascoolingcentral': 32, 'ac': 33, 'gasappliancesincluded': 34, 'gas': 35, 'water': 36, 'heaterlaundry': 37, 'main': 38, 'levelhttpswwwzillowcomhomedetails602-3rd-ave-deptford-nj-0809638761090zpid': 39, 'foreclosure199900bedrooms': 40, '2heatingpropanecoolinghas': 41, 'cooling': 42, 'yeslotsize': 43, '374': 44, 'acresdimensions': 45, 'acresdetailsparcel': 46, 'number': 47, '040006600000000111special': 48

In [23]:
def pad_sequences(indexed_texts, max_length=None):
    """
    Pad sequences to the same length with <PAD> token.
    """
    if not max_length:
        max_length = max(len(seq) for seq in indexed_texts)
    padded = [seq + [0] * (max_length - len(seq)) for seq in indexed_texts]
    return torch.tensor(padded, dtype=torch.long)

# Pad indexed descriptions
padded_descriptions = pad_sequences(indexed_descriptions)

In [27]:
class RecommendationModel(nn.Module):
    def __init__(self, vocab_size, embedding_dim, hidden_dim, output_dim):
        super(RecommendationModel, self).__init__()
        self.embedding = nn.Embedding(vocab_size, embedding_dim, padding_idx=0)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, batch_first=True)
        self.fc = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        embedded = self.embedding(x)
        lstm_out, _ = self.lstm(embedded)
        output = self.fc(lstm_out[:, -1, :])  # Use the last hidden state
        return output

# Hyperparameters
embedding_dim = 50
hidden_dim = 128
output_dim = 2  # Binary classification: Match or No Match
vocab_size = len(vocab)

# Instantiate the model
model = RecommendationModel(vocab_size, embedding_dim, hidden_dim, output_dim)
print(model)

RecommendationModel(
  (embedding): Embedding(22231, 50, padding_idx=0)
  (lstm): LSTM(50, 128, batch_first=True)
  (fc): Linear(in_features=128, out_features=2, bias=True)
)


In [28]:
user_preferences = [
    "Looking for a modern house with a backyard",
    "Seeking a small apartment near public transport",
    "Need a villa with luxury amenities",
    "Want a cozy cottage near the beach",
    "Looking for a studio apartment with easy access to the city center",
    "Looking for a spacious penthouse with panoramic views",
    "Searching for a house with a large kitchen and garden space",
    "Looking for a family-friendly apartment with a playground nearby",
    "Need a two-bedroom apartment with office space",
    "Searching for a home with energy-efficient features",
    "Looking for a modern townhouse with 3 bedrooms",
    "Need a home with easy access to schools and public transport",
    "Searching for a villa with a swimming pool and gym",
    "Looking for a pet-friendly house with a backyard",
    "Want an apartment with a home office and fast internet",
    "Need a property with ample parking space",
    "Searching for a home with a garden and close to hiking trails",
    "Looking for a luxurious property with a private spa",
    "Need a property in a quiet neighborhood with parks nearby",
    "Seeking an affordable apartment in the city center",
    "Looking for a new construction home with modern features",
    "Searching for a home near top-rated schools",
    "Want a house with a garage and extra storage space",
    "Looking for a property with smart home features",
    "Searching for a townhouse with a large garage",
    "Need a penthouse with a private rooftop terrace",
    "Looking for a property with stunning city views",
    "Need a house with a large backyard for outdoor activities",
    "Looking for an apartment with a large living room and kitchen",
    "Searching for a villa in a gated community with 24/7 security"
]

In [29]:
processed_preferences = [preprocess_text(pref) for pref in user_preferences]
indexed_preferences = tokens_to_indices(processed_preferences, vocab)
padded_preferences = pad_sequences(indexed_preferences)

In [30]:
def weighted_cosine_similarity(user_embedding, description_embeddings, weight_terms):
    """
    Compute weighted cosine similarity between the user input and description embeddings.
    Terms in `weight_terms` will increase the weight of the similarity calculation.
    """
    similarities = cosine_similarity(user_embedding, np.array(description_embeddings).squeeze())

    # Flatten similarities in case it's a 2D array (cosine_similarity can return 2D)
    similarities = similarities.flatten()

    # Weight the similarity based on key terms like "bedroom", "bathroom", etc.
    for i, description in enumerate(description_embeddings):
        description_text = descriptions[i]
        
        # Give extra weight to descriptions that match key terms with numbers
        for term in weight_terms:
            if term in description_text:
                # Increase similarity score by a factor for each key term found in the description
                similarities[i] += 1.5  # You can adjust this factor as needed

    return similarities

In [41]:
mapping = {"one": 1, "two": 2, "three": 3, "four": 4, "five": 5, "six": 6, "seven": 7, "eight": 8, "nine": 9, "ten": 10}

def find_important_terms(text):
    important_words = []
    pattern = r'(\d+|-?\b(?:one|two|three|four|five|six|seven|eight|nine|ten)\b)(-?)(\s*)(bedrooms|bathrooms|bedroom|bathroom)'
    for match in re.findall(pattern, text):
        # Reconstruct the exact match
        number = match[0]
        if number in mapping:
            number = mapping[number]
        room_type = match[3]
        reconstructed = f"{room_type}: {number}"
        important_words.append(reconstructed)
    pattern = r'\b(bathrooms?|bedrooms?):\s*(\d+|one|two|three|four|five|six|seven|eight|nine|ten)\b'
    for match in re.findall(pattern, text):
        # Reconstruct the exact match
        number = match[0]
        room_type = match[1]
        if number in mapping:
            number = mapping[number]
        reconstructed = f"{number}: {room_type}"
        important_words.append(reconstructed)


    return important_words

In [32]:
def recommend(user_input, model, descriptions, vocab):
    model.eval()
    # Preprocess using the new function that considers number-weighting
    processed_input = preprocess_text(user_input)
    indexed_input = tokens_to_indices([processed_input], vocab)
    padded_input = pad_sequences(indexed_input)
    
    with torch.no_grad():
        # Get the embedding for the user input
        embedded_input = model.embedding(padded_input)
        lstm_out, _ = model.lstm(embedded_input)
        user_embedding = lstm_out[:, -1, :].numpy()  # Use the last hidden state as the embedding

        # Get the embeddings for all descriptions
        description_embeddings = []
        for description in padded_descriptions:
            description_input = description.unsqueeze(0)  # Add batch dimension
            embedded_desc = model.embedding(description_input)
            lstm_out_desc, _ = model.lstm(embedded_desc)
            description_embeddings.append(lstm_out_desc[:, -1, :].numpy())

        # Define important terms to weight (e.g., "bedroom", "bathroom", "backyard")
        weight_terms = ["backyard","house", "apartment", "villa", "condo"]
        weight_terms.extend(find_important_terms(user_input))
        print(weight_terms)

        # Compute weighted cosine similarity between user input and all descriptions
        similarities = weighted_cosine_similarity(user_embedding, description_embeddings, weight_terms)

        # Find the index of the most similar description
        most_similar_idx = np.argmax(similarities)
        
    return descriptions[most_similar_idx]

In [44]:
# Example user input
user_input = "must have five bedrooms and three bathrooms, heating and hot water and upgraded countertops and  house with a backyard and a basement"
recommended = recommend(user_input, model, descriptions, vocab)
print("Recommended Property:", recommended)


['backyard', 'house', 'apartment', 'villa', 'condo', 'bedrooms: 5', 'bathrooms: 3']
Recommended Property: Foreclosure~$700,000~bedrooms & bathrooms||bedrooms: 5||bathrooms: 3||full bathrooms: 2||1/2 bathrooms: 1||main level bathrooms: 1~rooms||room types: living room, dining room, kitchen, family room~basement||area: 0~heating||90% forced air, natural gas~cooling||central a/c, natural gas~https://www.zillow.com/homedetails/3-Springhouse-Ct-Bordentown-NJ-08505/72245749_zpid/
